##Корпус антропологических интервью

*На основе tsakorpus*

Создаём из таблицы с данными об интервью и документов с расшифровками джейсоны для корпуса

**Document-level meta:** filename, title, author, recplace, year, month, day, informants_id, is_transcript, audio_links

**Sentence-level meta:** speaker


In [ ]:
! pip install python-docx
! pip install dropbox

import os
import docx
import re
import json
import pandas as pd

import nltk
from nltk.tokenize import word_tokenize
nltk.download('punkt')
import string
import itertools

import pathlib
import pandas as pd
import dropbox
from dropbox.exceptions import AuthError
import urllib

from google.colab import files
from datetime import date

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 35.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for python-docx: filename=python_docx-0.8.11-py3-none-any.whl size=184505 sha256=478a779f284ec621dc24fee3850f73629a6e1de2e92bad1b3991a8e0fc70e353
  Stored in directory: /root/.cache/pip/wheels/32/b8/b2/c4c2b95765e615fe139b0b17b5ea7c0e1b6519b0a9ec8fb34d
Successfully built python-docx
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 594.0/594.0 KB 6.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 162.3/162.3 KB 5.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 KB 3.2 MB/s eta 0:00:00


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


**Парсинг таблицы**

In [ ]:
import pathlib
import pandas as pd
import dropbox
from dropbox.exceptions import AuthError

In [ ]:
url = 'https://www.dropbox.com/sh/1d1stbh1t6wm4nw/AAAtFaXlLP0lglLRxcCFBgJ5a/%D1%82%D0%B5%D0%BA%D1%81%D1%82%D0%BE%D0%B2%D1%8B%D0%B5%20%D1%84%D0%B0%D0%B9%D0%BB%D1%8B%20%D0%BF%D0%BE%20%D0%B8%D1%82%D0%BE%D0%B3%D0%B0%D0%BC%20%D0%B8%D0%BD%D1%82%D0%B5%D1%80%D0%B2%D1%8C%D1%8E/%D0%B8%D0%BD%D1%82%D0%B5%D1%80%D0%B2%D1%8C%D1%8E%2025%20%D0%B8%D1%8E%D0%BD%D1%8F/%D0%92%D0%B0%D1%81%D0%B8%D0%BB%D0%B8%D1%81%D0%B0%20%D0%94%D1%91%D0%BC%D0%B8%D0%BD%D0%B0%20-%20%D0%9D%D0%B8%D0%BA%D0%B8%D1%82%D0%B0%20%D0%A1%D1%82%D0%B5%D0%BF%D0%B0%D0%BD%D0%BE%D0%B2.docx?dl=0'

**Достаём данные из таблицы**

! file = ИМЯ БАЗЫ В ЭКСЕЛЕ

In [ ]:
file = 'the_base.xlsx'

base = pd.ExcelFile(file)
print(base.sheet_names)

['информанты', 'интервью', 'интервьюеры (копия)', 'экспедиции', 'населённые пункты', 'информанты март 2021 (ПК, Елизо']


In [ ]:
base_interviews = base.parse('интервью')
base_interviews

/usr/local/lib/python3.8/dist-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Data Validation extension is not supported and will be removed
  warn(msg)


Код экспедиции Шифр для цитат (1-CUM22)  \
0   520          KAN21                520-KAN21   
1   521          KAN21                521-KAN21   
2   522          KAN21                522-KAN21   
3   523          KAN21                523-KAN21   
4   524          KAN21                524-KAN21   
5   525          KAN21                525-KAN21   
6   526          KAN21                526-KAN21   
7   527          KAN21                527-KAN21   
8   528          KAN21                528-KAN21   
9   529          KAN21                529-KAN21   
10  530          KAN21                530-KAN21   
11  531          KAN21                531-KAN21   
12  532          KAN21                532-KAN21   
13  533          KAN21                533-KAN21   
14  534          KAN21                534-KAN21   
15  535          KAN21                535-KAN21   
16  536          KAN21                536-KAN21   
17  537          KAN21                537-KAN21   
18  538          KAN21                538-KAN21   
19  539          KAN21                539-KAN21   
20  540          KAN21                540-KAN21   
21  541          KAN21                541-KAN21   
22  542          KAN21                542-KAN21   
23  543          KAN21                543-KAN21   
24  544          KAN21                544-KAN21   
25  545          KAN21                545-KAN21   
26  546          KAN21                546-KAN21   
27  547          KAN21                547-KAN21   
28  548          KAN21                548-KAN21   

                              Текущие названия файлов  \
0   даша морозова - 2021-11-22_Калевала_Галина Вил...   
1   даша морозова - 2021-11-23_Калевала_Людмила Са...   
2   даша морозова - 2021-11-23_Калевала_Ольга Бобр...   
3   даша морозова - 2021-11-23_Калевала_Юрий Алекс...   
4   даша морозова - 2021-11-24_Юшкозеро_Анна Васил...   
5   даша морозова - 2021-11-25_Калевала_Тамара Ива...   
6   даша морозова - 2021-11-26_Калевала_Владимир Л...   
7   Даша Морозова - 2021-11-26_Калевала_Владимир Л...   
8   Мария Лапина - 2021-11-21_Калевала_Галина Петр...   
9   Мария Лапина - 2021-11-22_Калевала_Ольга Кураш...   
10  Мария Лапина - 2021-11-23_Калевала_Валентина С...   
11  Мария Лапина - 2021-11-23_Калевала_Лайна Зинну...   
12  Мария Лапина - 2021-11-24_Юшкозеро_Полина Руби...   
13  Мария Лапина - 2021-11-24_Юшкозеро_Раиса Рыбак...   
14  Мария Лапина - 2021-11-24_Юшкозеро_Татьяна Лес...   
15  Полина - 2021-11-22_Калевала_Андрей, Александр...   
16  Полина - 2021-11-22_Калевала_Лайна Сергеевна_О...   
17  Полина - 2021-11-22_Калевала_Уборщица в Семёро...   
18  Полина - 2021-11-23_Калевала_Служительница пра...   
19  Полина - 2021-11-24_Юшкозеро_Андрей и Александ...   
20  Полина - 2021-11-24_Юшкозеро_Екатерина Алексан...   
21  Полина - 2021-11-25_Калевала_Васильева Надежда...   
22  Полина - 2021-11-25_Калевала_Тихонова Виктория...   
23  Полина - 2021-11-27_Калевала_Лесонен Алевтина ...   
24  Aleksei Ryzhkov - 2021-11-27_Калевала_Иван Мал...   
25  Aleksei Ryzhkov - Aleksei Ryzhkov - 2021-11-25...   
26  Anastasiya Smirnova - 2021-11-21_Калевала_Прод...   
27  Anastasiya Smirnova - 2021-11-22_Калевала_Серг...   
28  Anastasiya Smirnova - 2021-11-26_Калевала_Нина...   

                            Длины файлов  \
0                      0:37:41, 00:37:53   
1                               00:32:13   
2   1:02:08, 0:10:33, 01:49:54, 01:48:20   
3                      1:02:08, 00:55:19   
4                      1:03:20, 01:23:42   
5            0:34:41, 00:42:56, 01:17:33   
6                      2:49:59, 02:48:31   
7            0:20:37, 00:05:10, 00:42:04   
8                      1:31:38, 01:27:45   
9                               00:48:44   
10                     0:16:15, 00:41:54   
11                              00:51:27   
12                              01:35:36   
13                     0:55:56, 00:03:06   
14                              00:27:24   
15                              00:10:35   
16                

In [ ]:
len(base_interviews)

29

In [ ]:
base_interviews['Текущие названия файлов'][0]

'даша морозова - 2021-11-22_Калевала_Галина Вилховна_Морозова, Недайхлеб.WAV, Полина - 2021-11-22_Калевала_Галина Вилховна_Морозова, Недайхлеб.MP3'

In [ ]:
base_interviews['Ссылка на расшифровку'][0]

'https://www.dropbox.com/sh/ggznkk19jn7k4gm/AAAz2nWm3Uy9G6EaUZdKhnoNa/Anastasia%20Smirnova%20-%202021-11-22_Калевала_Галина%20Вилховна_Морозова%2C%20Недайхлеб.docx?dl=0'

In [ ]:
import pathlib
import pandas as pd
import dropbox
from dropbox.exceptions import AuthError
from dropbox import DropboxOAuth2FlowNoRedirect

Подключение в DropBoxAPI

In [ ]:
APP_KEY = APP_KEY
APP_SECRET = APP_SECRET
auth_flow = DropboxOAuth2FlowNoRedirect(APP_KEY, APP_SECRET)
authorize_url = auth_flow.start()
print ("1. Go to: " + authorize_url)
print ("2. Click \"Allow\" (you might have to log in first).")
print ("3. Copy the authorization code.")
auth_code = input("Enter the authorization code here: ").strip()
try:
 oauth_result = auth_flow.finish(auth_code)
except Exception as e:
  print("Error: %s" % (e,))

1. Go to: https://www.dropbox.com/oauth2/authorize?response_type=code&client_id=55pknt48n0zltjr
2. Click "Allow" (you might have to log in first).
3. Copy the authorization code.
Enter the authorization code here: rXidN-vZ2ZAAAAAAAAAAHkKbKjHWFhv12BPQmMGLkzA


In [ ]:
dbx = dropbox.Dropbox("ACCESS_TOKEN")

**Пример работы со ссылкой:**

Норм ссылка:

In [ ]:
url = "https://www.dropbox.com/sh/ggznkk19jn7k4gm/AAAz2nWm3Uy9G6EaUZdKhnoNa/Anastasia%20Smirnova%20-%202021-11-22_%D0%9A%D0%B0%D0%BB%D0%B5%D0%B2%D0%B0%D0%BB%D0%B0_%D0%93%D0%B0%D0%BB%D0%B8%D0%BD%D0%B0%20%D0%92%D0%B8%D0%BB%D1%85%D0%BE%D0%B2%D0%BD%D0%B0_%D0%9C%D0%BE%D1%80%D0%BE%D0%B7%D0%BE%D0%B2%D0%B0%2C%20%D0%9D%D0%B5%D0%B4%D0%B0%D0%B9%D1%85%D0%BB%D0%B5%D0%B1.docx?dl=0"

НЕ норм ссылка:

Ссылка должна быть без букв кириллицы, поэтому мы её перекодируем

In [ ]:
url = "https://www.dropbox.com/sh/ggznkk19jn7k4gm/AAAz2nWm3Uy9G6EaUZdKhnoNa/Anastasia%20Smirnova%20-%202021-11-22_Калевала_Галина%20Вилховна_Морозова%2C%20Недайхлеб.docx?dl=0"

In [ ]:
reg_bad_url = re.compile("https:\/\/www\.dropbox\.com\/sh\/.*\/(.*)\.docx")
reg_right_url_part = re.compile("(https:\/\/www\.dropbox\.com\/sh\/.*\/).*\.docx")

In [ ]:
right_url_part = re.findall(reg_right_url_part, url)[0]
print(right_url_part)

https://www.dropbox.com/sh/ggznkk19jn7k4gm/AAAz2nWm3Uy9G6EaUZdKhnoNa/


In [ ]:
bad_name = re.findall(reg_bad_url, url)[0]
bad_name = bad_name.replace("%20", " ")
bad_name = bad_name.replace("%2C", ",")
print(bad_name)

Anastasia Smirnova - 2021-11-22_Калевала_Галина Вилховна_Морозова, Недайхлеб


In [ ]:
right_name = urllib.parse.quote(bad_name)
print(right_name)

Anastasia%20Smirnova%20-%202021-11-22_%D0%9A%D0%B0%D0%BB%D0%B5%D0%B2%D0%B0%D0%BB%D0%B0_%D0%93%D0%B0%D0%BB%D0%B8%D0%BD%D0%B0%20%D0%92%D0%B8%D0%BB%D1%85%D0%BE%D0%B2%D0%BD%D0%B0_%D0%9C%D0%BE%D1%80%D0%BE%D0%B7%D0%BE%D0%B2%D0%B0%2C%20%D0%9D%D0%B5%D0%B4%D0%B0%D0%B9%D1%85%D0%BB%D0%B5%D0%B1


In [ ]:
right_url = right_url_part + right_name + ".docx?dl=0"
print(right_url)

https://www.dropbox.com/sh/ggznkk19jn7k4gm/AAAz2nWm3Uy9G6EaUZdKhnoNa/Anastasia%20Smirnova%20-%202021-11-22_%D0%9A%D0%B0%D0%BB%D0%B5%D0%B2%D0%B0%D0%BB%D0%B0_%D0%93%D0%B0%D0%BB%D0%B8%D0%BD%D0%B0%20%D0%92%D0%B8%D0%BB%D1%85%D0%BE%D0%B2%D0%BD%D0%B0_%D0%9C%D0%BE%D1%80%D0%BE%D0%B7%D0%BE%D0%B2%D0%B0%2C%20%D0%9D%D0%B5%D0%B4%D0%B0%D0%B9%D1%85%D0%BB%D0%B5%D0%B1.docx?dl=0


Обращение к дропбоксу

In [ ]:
md, res = dbx.sharing_get_shared_link_file(url=right_url)

In [ ]:
res

<Response [200]>

значит, всё ок

md = метаданные, res - содержание

Запишем содержание в ворд, чтобы распарсить

In [ ]:
with open("int1.docx", "wb") as f:
    f.write(res.content)

**Функция парсинга:**

Принимает на вход расшифровку интервью, возвращает список предложений

In [ ]:
! pip install natasha

from natasha import (
    Segmenter,
    MorphVocab,

    NewsEmbedding,
    NewsMorphTagger,
    NewsSyntaxParser,
    NewsNERTagger,
    
    PER,
    NamesExtractor,
    Doc
)


segmenter = Segmenter()
morph_vocab = MorphVocab()

segmenter = Segmenter()
morph_vocab = MorphVocab()

emb = NewsEmbedding()
morph_tagger = NewsMorphTagger(emb)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
def parse(path, infs, ints):
  #отрывки
  reg_line = re.compile("Ин..?:.*")
  reg_speaker = re.compile("(Ин..?):.*")
  reg_number = re.compile("\d")
  reg_saying = re.compile("Ин..?:\s?(.*)") 

  #достаём текст
  doc = docx.Document(path)
  text = []
  for paragraph in doc.paragraphs:
      text.append(paragraph.text)
  print(text)
  text = '\n'.join(text)
  speakers_di = {}

  sentences_list = []
  lines = re.findall(reg_line, text)
  for line in lines:
    sentence_di = {}
    sentence_di["lang"] = 0
    saying = re.findall(reg_saying, line)[0]
    speaker = re.findall(reg_speaker, line)[0]
    if 'Инт' in speaker:
      int_number = int(re.findall(reg_number, speaker)[0])
      int_number -= 1
      try:
        speaker = ints[int_number]
      except IndexError:
        speaker = 'Somebody'
    elif 'Инф' in speaker:
      inf_number = int(re.findall(reg_number, speaker)[0])
      inf_number -= 1
      try:
        speaker = infs[inf_number]
      except IndexError:
        speaker = 'Somebody'
    else:
      speaker = 'Somebody'

    sentence_meta_di = {}
    sentence_meta_di["speaker"] = speaker
    sentence_di["text"] = saying
    sentences_list.append(sentence_di)
    words = []
    li = [[word_tokenize(w), ' '] for w in saying.split()]
    tokens = list(itertools.chain(*list(itertools.chain(*li))))
    index = 0
    off_start = 0
    prev_space = 0
    word_counter = 0
    for word in tokens:
      word_di = {}
      word_di["wf"] = word
      if word in string.punctuation:
        word_di["wtype"] = "punct"
      elif word == ' ':
        prev_space = 1
      else:
        word_di["wtype"] = "word"
        word_counter += 1
        
      if prev_space == 1:
        off_start = off_start + 1
        prev_space = 0
      
      if word != ' ':
        word_di["off_start"] = off_start
        off_end = off_start + len(word)
        word_di["off_end"] = off_end
        off_start = off_end
        index += 1
        word_di["next_word"] = index
        
      if word != ' ':
        words.append(word_di)
    
    snt_indx = 0
    for word in words:
      if word['wtype'] == 'word':
        word["sentence_index_neg"] = word_counter
        word_counter -= 1
      if word['wtype'] != 'punct':
        word["sentence_index"] = snt_indx
        snt_indx += 1
      elif word['wtype'] == 'punct' and word['off_start'] != 0 and word['next_word'] < len(words):
        word["sentence_index"] = snt_indx
        snt_indx += 1
    
    sentence_di["words"] = words
    sentence_di["meta"] = sentence_meta_di

  return sentences_list

In [ ]:
def morph_analyse(sentence):
  ana_list = []
  seq = sentence
  doc = Doc(seq)
  doc.segment(segmenter)
  doc.tag_morph(morph_tagger)
  ana_di = {}
  for token in doc.tokens:
    print(token.feats)
    ana_di["lex"] = token.text
    ana_di["gr.pos"] = token.pos
    if 'Animacy' in token.feats.keys():
      ana_di["gr.anim"] = token.feats['Animacy']
    if 'Case' in token.feats.keys():
      ana_di["gr.case"] = token.feats['Case']
    if 'Number' in token.feats.keys():
      ana_di["gr.number"] = token.feats['Number']
    if 'Person' in token.feats.keys():
      ana_di["gr.person"] = token.feats['Person']
    if 'Aspect' in token.feats.keys():
      ana_di["gr.aspect"] = token.feats['Aspect']
    if 'Mood' in token.feats.keys():
      ana_di["gr.mood"] = token.feats['Mood']
    if 'Tense' in token.feats.keys():
      ana_di["gr.tense"] = token.feats['Tense']
    if 'VerbForm' in token.feats.keys():
      ana_di["gr.verbform"] = token.feats['VerbForm']
    if 'Voice' in token.feats.keys():
      ana_di["gr.voice"] = token.feats['Voice']
    if 'Degree' in token.feats.keys():
      ana_di["gr.degree"] = token.feats['Degree']
    ana_list.append(ana_di)
    ana_di = {}
  return ana_list

In [ ]:
sentences_list = parse('int1.docx', ['i1'], ['DM', 'PN'])
meta_di = {}
meta_di["filename"] = "int1.docx"
meta_di["title"] = "5"
meta_di["author"] = "DAM, PAN"
meta_di['recplace'] = "Калевала"
meta_di["year"] = 2021

json_di = {"meta" : meta_di, "sentences" : sentences_list}
with open("example_words.json", "w", encoding='utf-8') as jsonfile:
        json.dump(json_di, jsonfile, ensure_ascii=False)

**Код, который проходится по всем интервью из таблицы, записывает их метаданные (из таблицы) и парсит расшифровку (если она есть). Всё записывается в json и скачивается на компьютер. 1 json = 1 интервью**

In [ ]:
reg_bad_url = re.compile("https:\/\/www\.dropbox\.com\/sh\/.*\/(.*)\.docx")
reg_right_url_part = re.compile("(https:\/\/www\.dropbox\.com\/sh\/.*\/).*\.docx")

for i in range(len(base_interviews)):
  file_di = {}
  all_files = base_interviews['Текущие названия файлов'][i]
  expedition = base_interviews['Код экспедиции'][i]
  interview_citation = base_interviews['Шифр для цитат (1-CUM22)'][i]
  audio_links = base_interviews['Ссылка на аудио'][i].split(',')
  recording_data = base_interviews['Дата записи интервью'][i]
  year = int(recording_data.strftime("%Y"))
  month = int(recording_data.strftime("%m"))
  day = int(recording_data.strftime("%d"))
  recording_place = base_interviews['Место записи интервью (НАСЕЛЁННЫЙ ПУНКТ)'][i]
  interviewers = base_interviews['Интервьюеры'][i].split(',')
  concern = base_interviews['Согласие на запись'][i]
  is_transcript = base_interviews['Расшифровка'][i]
  transcript_format = base_interviews['Формат расшифровки'][i]
  inf1 = base_interviews['ИНФ1 (основной) (СТРОГО ФИО)'][i]
  inf2 = base_interviews['ИНФ2 (основной)'][i]
  inf3 = base_interviews['ИНФ3 (основной)'][i]
  inf4 = base_interviews['ИНФ4'][i]
  inf5 = base_interviews['ИНФ5'][i]
  inf6 = base_interviews['ИНФ6'][i]
  inf7 = base_interviews['ИНФ7'][i]
  informants = [inf1, inf2, inf3, inf4, inf5, inf6, inf7]
  true_informants = []
  for inf in informants:
    if type(inf) == str:
      true_informants.append(inf)
  meta_di = {}
  meta_di["title"] = interview_citation
  meta_di["year"] = year
  meta_di["month"] = month
  meta_di["day"] = day
  meta_di["place"] = recording_place
  meta_di["interviewers"] = ", ".join(interviewers)
  meta_di["filename"] = interview_citation
  #filename не будет видно в корпусе
  meta_di["informants"] = ", ".join(true_informants)
  #if transcript_format != '':
   # is_transcript = is_transcript + ', ' + transcript_format
  meta_di["is_transcript"] = is_transcript
  meta_di["audio_links"] = audio_links
  file_di["meta"] = meta_di

  #парсим расшифровку, если она есть
  wrong_links = []
  print(is_transcript)
  if is_transcript == 'есть':
    #and transcript_format == 'дословная'
    transcript_links = base_interviews['Ссылка на расшифровку'][i].split(',')
    for url in transcript_links:
      if "preview" not in url:
        right_url_part = re.findall(reg_right_url_part, url)[0]
        bad_name = re.findall(reg_bad_url, url)[0]
        bad_name = bad_name.replace("%20", " ")
        bad_name = bad_name.replace("%2C", ",")
        right_name = urllib.parse.quote(bad_name)
        right_url = right_url_part + right_name + ".docx?dl=0"
        md, res = dbx.sharing_get_shared_link_file(url=right_url)
        with open("int_text.docx", "wb") as f:
          print('i-m parsing')
          f.write(res.content)
          sentences_list = parse("int_text.docx", true_informants, interviewers)
        file_di["sentences"] = sentences_list
      else:
        wrong_links.append(url)
      print(file_di)
  else:
    file_di["sentences"] = [] 
  with open("inf" + str(i) + ".json", "w", encoding='utf-8') as jsonfile:
        json.dump(file_di, jsonfile, ensure_ascii=False)
  files.download("inf" + str(i) + ".json")

есть
i-m parsing
['Номер интервью в базе: 5', 'Инт1 — Дарья Морозова', 'Инт2 — Полина Недайхлеб', 'Инф1 — ж, ? г. р.', 'Место: посёлок городского типа Калевала', 'Дата: 22.1.2021.', '', 'Инт1: А вы, получается, вы здесь родились?', 'Инф1: Ну да, я родилась вообще в Калевальском районе, и дальше вот отсюда есть деревня, называется Войница, шестьдесят километров в сторону Костомукши, вот я родом оттуда.', '', 'Инт1: А как вы вот сюда попали?', 'Инф1: Здесь я вообще жила, училась здесь, в Калевале, и как бы. Здесь и родилась, и здесь живу, как бы работаю.', '', 'Инт1: А родились вы в карельской семье?\nИнф1: Да, мать была карелка, ну отец тоже карел.', '', 'Инт1: А говорили они в семье…', 'Инф1: Говорили в семье мы с детства по-карельски. Я знала два языка, я даже не понимала. Как сказать, я росла, попутно я говорила и по-карельски, и по-русски. А училась, вот мы в деревне там в Войнице жили, и учились, мы сюда ездили в интернат, потому что школа там была до четырёх классов, и вот так мы…

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

есть
i-m parsing
['Номер интервью в базе: 19', 'Инт1 — Дарья Морозова', 'Инт2 — Полина Недайхлеб', 'Инф1 — ж, 1950 г. р.', 'Место: посёлок городского типа Калевала', 'Дата: 23.11.2021.', '', 'Инт1: А вы здесь, получается, родились? Ну, в смысле, в Калевале?', 'Инф1: Нет, я в деревне Вокнаволок.', 'Инт1: А сюда как попали?', 'Инф1: Ну, работать, там, возможно.', '', 'Инт1: А кем вы работали?', 'Инф1: Кем я работала? Поваром работала, кладовщиком работала, в лесу работала, везде работала.', '', 'Инт1: Ага, а вы родились в карельской семье, да?', 'Инф1: Да.', 'Инт1: И дома разговаривали по-карельски?', 'Инф1: Чисто по-карельски. В школу пошли не знали ни “а”, ни “б”.', '', 'Инт1: А тяжело было учить русский?', 'Инф1: А не помню уже. Учились все. Все там же были в деревне карелы. Там и сейчас больше говорят по-карельски в деревне, вам туда надо попасть.', '', 'Инт1: А здесь мало говорят?', 'Инф1: Да нет, говорят и тут.', 'Инт1: То есть, если вы видитесь с кем-то, кто говорит по-карельски, 

<IPython.core.display.Javascript object>

...

есть
i-m parsing
['Номер интервью в базе: 25', 'Инт1 —\xa0Дарья Олейник', 'Инт2 —\xa0Матвей Мордасов', 'Инт3 — Алексей Рыжков', 'Инф1 —\xa0ж., примерно 1966 г. р., директорка музыкальной школы', 'Инф2 —\xa0ж., примерно 1980 г. р., преподавательница фортепиано', 'Место: пгт Калевала Калевальского района', 'Дата: 26.11.2021', '', 'Инф1: Здание типового финского жилого дома. Это сауна, здесь была печка. Построено в конце 90-х годов, то есть 98-99 год. Но здание строилось калевальскими студентами, которые обучались на курсах строителей в Финляндии. И по проекту совместно они построили вот на территории Калевалы, вот такой типичный жилой дом. Но изначально знали, что здесь располагаться будет детская консультация, поликлиника. Хотя вот в таком типовом доме. Мы переехали сюда, поликлиника была с двухтысячных годов, 2000-2001, как-то так, мы переехали сюда в 2015 году. Поэтому нам пришлось здесь демонтировать, здесь сделать выход. Здесь сауна у нас, здесь душевая была по финскому. То есть в к

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Неверные ссылки: []


In [ ]:
for i in range (0, 29):
  files.download("inf" + str(i) + ".json")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>